# Databaze


- databaze pod jinym uzivatelem


- kurzor = prostredi, ve kterem se vykonavaji dotazy
    - lze jich mit vice
    - lze mit vice dotazu v ruznych stavech
    - cursor drzi v sobe vysledky a to, kde je


- transakce musi byt atomicke
    - v error stavu zamrzne pripojeni -> rollback
    - commit ... pokyn k zapsani do tabulky

In [12]:
from rdkit.Chem import AllChem as Chem
import psycopg2 as pg

import pickle

import rdkit.Chem.Draw as Draw
from rdkit.Chem.Draw import IPythonConsole

In [4]:
#pripojeni k DB v instanci c
c = pg.connect('dbname=drugbank user=script password=pnl') 

In [5]:
#kurzor v objektu cursor
cursor=c.cursor()

In [6]:
#test funkcnosti rdkit cartridge
#jako kdybychom to naspali do query DB
cursor.execute("select mol_numatoms('COO'::mol)")
cursor.fetchall() #vrati celou tabulku; u velke tabulky pres to lze iterovat

[(7,)]

In [7]:
cursor.execute("select mol_numatoms('CCO'::mol)")
cursor.fetchall()

[(9,)]

In [8]:
#ted nic neudela -> zadna zaseknuta transakce
c.rollback()

## Vyplneni databaze


- vztah M:N -> 3 tabulky dekompozici:
    - tabulka molekul ... molecules
    - tabulka skupin ... groups
    - spojovaci tabulka ... molecules2groups
    

- scaffold - struktura a ukazujici na misto v molecules

In [9]:
suppl = Chem.SDMolSupplier('../data/drugbank.sdf')
drugbank = [mol for mol in suppl if mol]

In [10]:
len(drugbank)

7110

In [11]:
#informace ve sloupcich v drugbank
#vysledek: set vsech informaci, ktere mohou byt v sdf (nad ramce ciste chemickych dat)
possible_columns = set()
for m in drugbank:
    possible_columns.update(m.GetPropsAsDict())
possible_columns    

{'ALOGPS_LOGP',
 'ALOGPS_LOGS',
 'ALOGPS_SOLUBILITY',
 'DATABASE_ID',
 'DATABASE_NAME',
 'DRUGBANK_ID',
 'DRUG_GROUPS',
 'EXACT_MASS',
 'FORMULA',
 'GENERIC_NAME',
 'INCHI_IDENTIFIER',
 'INCHI_KEY',
 'INTERNATIONAL_BRANDS',
 'JCHEM_ACCEPTOR_COUNT',
 'JCHEM_ATOM_COUNT',
 'JCHEM_AVERAGE_POLARIZABILITY',
 'JCHEM_BIOAVAILABILITY',
 'JCHEM_DONOR_COUNT',
 'JCHEM_FORMAL_CHARGE',
 'JCHEM_GHOSE_FILTER',
 'JCHEM_IUPAC',
 'JCHEM_LOGP',
 'JCHEM_MDDR_LIKE_RULE',
 'JCHEM_NUMBER_OF_RINGS',
 'JCHEM_PHYSIOLOGICAL_CHARGE',
 'JCHEM_PKA',
 'JCHEM_PKA_STRONGEST_ACIDIC',
 'JCHEM_PKA_STRONGEST_BASIC',
 'JCHEM_POLAR_SURFACE_AREA',
 'JCHEM_REFRACTIVITY',
 'JCHEM_ROTATABLE_BOND_COUNT',
 'JCHEM_RULE_OF_FIVE',
 'JCHEM_TRADITIONAL_IUPAC',
 'JCHEM_VEBER_RULE',
 'MOLECULAR_WEIGHT',
 'PRODUCTS',
 'SALTS',
 'SECONDARY_ACCESSION_NUMBERS',
 'SMILES',
 'SYNONYMS'}

- informace, ktere nejsou 1:1
    - synonyma ... 1:N
    - soli
    - produkty 

### tabulka drugbank.molecules

In [14]:
#nadefinujeme sloupce, ktere by to melo mit
molecule_columns = (
 'ALOGPS_LOGP',
 'ALOGPS_LOGS',
 'ALOGPS_SOLUBILITY',
 'DATABASE_ID',
 'DATABASE_NAME',
 'DRUGBANK_ID',
 'EXACT_MASS',
 'FORMULA',
 'GENERIC_NAME',
 'INCHI_IDENTIFIER',
 'INCHI_KEY',
 'JCHEM_ACCEPTOR_COUNT',
 'JCHEM_ATOM_COUNT',
 'JCHEM_AVERAGE_POLARIZABILITY',
 'JCHEM_BIOAVAILABILITY',
 'JCHEM_DONOR_COUNT',
 'JCHEM_FORMAL_CHARGE',
 'JCHEM_GHOSE_FILTER',
 'JCHEM_IUPAC',
 'JCHEM_LOGP',
 'JCHEM_MDDR_LIKE_RULE',
 'JCHEM_NUMBER_OF_RINGS',
 'JCHEM_PHYSIOLOGICAL_CHARGE',
 'JCHEM_PKA',
 'JCHEM_PKA_STRONGEST_ACIDIC',
 'JCHEM_PKA_STRONGEST_BASIC',
 'JCHEM_POLAR_SURFACE_AREA',
 'JCHEM_REFRACTIVITY',
 'JCHEM_ROTATABLE_BOND_COUNT',
 'JCHEM_RULE_OF_FIVE',
 'JCHEM_TRADITIONAL_IUPAC',
 'JCHEM_VEBER_RULE',
 'MOLECULAR_WEIGHT',
 'SMILES')

#### sprava DB v "reset_drugbank.sql"
- zakladani tabulek atd.


#### vyplneni tabulky molecules molekulami z drugbank:

In [27]:
def molecule2insertstring(mol, columns):
    values = []
    for c in columns:
        try:
            # vkladani dat do tabulky: hodnoty oddelene '' 
            #jelikoz jsou ' ve vzorcich, tak se musi zdvojit (jako escape character)
            value = "'{}'".format(mol.GetProp(c).replace("'","''")) 
        except KeyError:
            value = 'null'
        values.append(value)
    return "({})".format(", ".join(values))


In [28]:
molecule2insertstring(drugbank[666],molecule_columns)

"('2.66', '-6.75', '7.22e-05 g/l', 'DB00782', 'drugbank', 'DB00782', '368.222568831', 'C23H30NO3', 'Propantheline', 'InChI=1S/C23H30NO3/c1-16(2)24(5,17(3)4)14-15-26-23(25)22-18-10-6-8-12-20(18)27-21-13-9-7-11-19(21)22/h6-13,16-17,22H,14-15H2,1-5H3/q+1', 'VVWYOYDLCMFIEM-UHFFFAOYSA-N', '1', null, '40.86703349207315', '1', '0', '1', '1', 'methylbis(propan-2-yl)[2-(9H-xanthene-9-carbonyloxy)ethyl]azanium', '0.3637936438615875', '1', '3', '1', null, '18.098024207383688', '-7.185977917412988', '35.53', '119.25450000000001', '7', '1', 'propantheline', '1', '368.4892', 'CC(C)[N+](C)(CCOC(=O)C1C2=CC=CC=C2OC2=CC=CC=C12)C(C)C')"

In [29]:
#priprava prikazu
query = "insert into drugbank.molecule ({}) values {}".format(
    ", ".join(molecule_columns),                                                          
    ", ".join((molecule2insertstring(mol, molecule_columns) for mol in drugbank)))

In [37]:
#query

"insert into drugbank.molecule (ALOGPS_LOGP, ALOGPS_LOGS, ALOGPS_SOLUBILITY, DATABASE_ID, DATABASE_NAME, DRUGBANK_ID, EXACT_MASS, FORMULA, GENERIC_NAME, INCHI_IDENTIFIER, INCHI_KEY, JCHEM_ACCEPTOR_COUNT, JCHEM_ATOM_COUNT, JCHEM_AVERAGE_POLARIZABILITY, JCHEM_BIOAVAILABILITY, JCHEM_DONOR_COUNT, JCHEM_FORMAL_CHARGE, JCHEM_GHOSE_FILTER, JCHEM_IUPAC, JCHEM_LOGP, JCHEM_MDDR_LIKE_RULE, JCHEM_NUMBER_OF_RINGS, JCHEM_PHYSIOLOGICAL_CHARGE, JCHEM_PKA, JCHEM_PKA_STRONGEST_ACIDIC, JCHEM_PKA_STRONGEST_BASIC, JCHEM_POLAR_SURFACE_AREA, JCHEM_REFRACTIVITY, JCHEM_ROTATABLE_BOND_COUNT, JCHEM_RULE_OF_FIVE, JCHEM_TRADITIONAL_IUPAC, JCHEM_VEBER_RULE, MOLECULAR_WEIGHT, SMILES) values ('-0.76', '-4.67', '4.64e-02 g/l', 'DB00006', 'drugbank', 'DB00006', '2178.985813062', 'C98H138N24O33', 'Bivalirudin', 'InChI=1S/C98H138N24O33/c1-5-52(4)82(96(153)122-39-15-23-70(122)92(149)114-60(30-34-79(134)135)85(142)111-59(29-33-78(132)133)86(143)116-64(43-55-24-26-56(123)27-25-55)89(146)118-67(97(154)155)40-51(2)3)119-87(14

In [32]:
c.rollback()
cursor.execute(query)

In [33]:
c.commit()

In [39]:
cursor.execute("select count(*) from drugbank.molecule")
cursor.fetchall()

[(7110,)]